In [1]:
%cd yolor

C:\Users\user\Desktop\jh\yolor


# Fix Seed

In [44]:
import torch
import numpy as np
import random
import os

def my_seed_everywhere(seed: int = 42):
    random.seed(seed) # random
    np.random.seed(seed) # numpy
    os.environ["PYTHONHASHSEED"] = str(seed) # os
    # pytorch
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed) 
    torch.backends.cudnn.deterministic = True 
    torch.backends.cudnn.benchmark = False 

my_seed = 42
my_seed_everywhere(my_seed)
print("Seed Fixed!")

Seed Fixed!


# Prepare Datasets

In [1]:
from glob import glob

img_list = glob('../dataset/train-001/images/*.png')
print("Total Image Number:", len(img_list))

Total Image Number: 24650


In [2]:
from sklearn.model_selection import train_test_split

train_img_list, val_img_list = train_test_split(img_list, test_size=0.05, random_state=42)

print("Train and Val Image Number:", len(train_img_list), len(val_img_list))

Train and Val Img Number: 23417 1233


In [47]:
with open('../dataset/train-001/train.txt', 'w', encoding='utf8') as f:
    f.write('\n'.join(train_img_list) + '\n')

with open('../dataset/train-001/val.txt', 'w', encoding='utf8') as f:
    f.write('\n'.join(val_img_list) + '\n')

In [11]:
# train val data Location Setting in YAML file
import yaml

data = {}
data['train'] = '../dataset/train-001/train.txt'
data['val'] = '../dataset/train-001/val.txt'
data['test'] = '../dataset/test-002/images'
data['nc'] = 14
data['names'] = ['세단(승용차)', 'SUV', '승합차', '버스', '학원차량(통학버스)', '트럭', '택시', '성인', '어린이', '오토바이', '전동킥보드', '자전거', '유모차', '쇼핑카트']


with open('../dataset/train-001/data.yaml', 'w', encoding='utf8') as f:
    yaml.dump(data, f)

print(data)

{'train': '../dataset/train-001/train.txt', 'val': '../dataset/train-001/val.txt', 'test': '../dataset/test-002/images', 'nc': 14, 'names': ['세단(승용차)', 'SUV', '승합차', '버스', '학원차량(통학버스)', '트럭', '택시', '성인', '어린이', '오토바이', '전동킥보드', '자전거', '유모차', '쇼핑카트']}


In [49]:
# Create 'data.names' file for model
import yaml
import ast

with open("../dataset/train-001/data.yaml", 'r') as stream:
    names = str(yaml.safe_load(stream)['names'])

namesFile = open("../dataset/train-001/data.names", "w+", encoding='utf8')
names = ast.literal_eval(names)
for name in names:
    namesFile.write(name +'\n')
namesFile.close()

In [50]:
import yaml

with open("../dataset/train-001/data.yaml") as f:
    dataMap = yaml.safe_load(f)

num_classes = len(dataMap['names'])
num_filters = (num_classes + 5) * 3

from IPython.core.magic import register_line_cell_magic

@register_line_cell_magic
def writetemplate(line, cell):
    with open(line, 'w') as f:
        f.write(cell.format(**globals()))

# COCO Json to YOLO Txt

In [64]:
import os
import json
from tqdm import tqdm
import shutil

def convert_bbox_coco2yolo(img_width, img_height, bbox):
    """
    Convert bounding box from COCO  format to YOLO format

    Parameters
    ----------
    img_width : int
        width of image
    img_height : int
        height of image
    bbox : list[int]
        bounding box annotation in COCO format: 
        [top left x position, top left y position, width, height]

    Returns
    -------
    list[float]
        bounding box annotation in YOLO format: 
        [x_center_rel, y_center_rel, width_rel, height_rel]
    """
    
    # YOLO bounding box format: [x_center, y_center, width, height]
    # (float values relative to width and height of image)
    x_tl, y_tl, w, h = bbox

    dw = 1.0 / img_width
    dh = 1.0 / img_height

    x_center = x_tl + w / 2.0
    y_center = y_tl + h / 2.0

    x = x_center * dw
    y = y_center * dh
    w = w * dw
    h = h * dh

    return [x, y, w, h]

def make_folders(path="output"):
    if os.path.exists(path):
        shutil.rmtree(path)
    os.makedirs(path)
    return path


def convert_coco_json_to_yolo_txt(output_path, json_file):

    path = make_folders(output_path)

    with open(json_file, encoding='utf-8') as f:
        json_data = json.load(f)

    # write _darknet.labels, which holds names of all classes (one class per line)
    label_file = os.path.join(output_path, "data.names")
    with open(label_file, "w", encoding='utf-8') as f:
        for category in tqdm(json_data["categories"], desc="Categories"):
            category_name = category["name"]
            f.write(f"{category_name}\n")

    for image in tqdm(json_data["images"], desc="Annotation txt for each iamge"):
        img_id = image["id"]
        img_name = image["file_name"]
        img_width = image["width"]
        img_height = image["height"]

        anno_in_image = [anno for anno in json_data["annotations"] if anno["image_id"] == img_id]
        anno_txt = os.path.join(output_path, img_name.split(".")[0] + ".txt")
        with open(anno_txt, "w", encoding='utf-8') as f:
            for anno in anno_in_image:
                category = anno["category_id"] - 1
                bbox_COCO = anno["bbox"]
                x, y, w, h = convert_bbox_coco2yolo(img_width, img_height, bbox_COCO)
                f.write(f"{category} {x:.6f} {y:.6f} {w:.6f} {h:.6f}\n")

    print("Converting COCO Json to YOLO txt finished!")

In [65]:
convert_coco_json_to_yolo_txt("../dataset/train-001/labels", "../dataset/train-001/label/Train.json")

Annotation txt for each iamge: 100%|████████████████████████████████████████████| 24650/24650 [02:49<00:00, 145.07it/s]

Converting COCO Json to YOLO txt finished!


# Train

In [20]:
%pwd

'C:\\Users\\user\\Desktop\\jh\\yolor'

In [1]:
%cd yolor

C:\Users\user\Desktop\jh\yolor


In [32]:
!python train.py --batch-size 8 --img 1280 1280 --data "../dataset/train-001/data.yaml" --cfg cfg/yolor_p6.cfg --weights yolor_p6.pt --device 0 --name yolor-220612 --hyp data/hyp.scratch.1280.yaml --epochs 25

Transferred 850/862 items from yolor_p6.pt
                 all    1.23e+03    6.94e+03       0.408        0.72       0.654       0.473
                 all    1.23e+03    6.94e+03       0.417       0.754       0.666       0.481

Using torch 1.11.0 CUDA:0 (NVIDIA GeForce RTX 3090, 24575MB)

Namespace(adam=False, batch_size=8, bucket='', cache_images=False, cfg='cfg/yolor_p6.cfg', data='../dataset/train-001/data.yaml', device='0', epochs=25, evolve=False, exist_ok=False, global_rank=-1, hyp='data/hyp.scratch.1280.yaml', image_weights=False, img_size=[1280, 1280], local_rank=-1, log_imgs=16, multi_scale=False, name='yolor-220612', noautoanchor=False, nosave=False, notest=False, project='runs/train', rect=False, resume=False, save_dir='runs\\train\\yolor-220612', single_cls=False, sync_bn=False, total_batch_size=8, weights='yolor_p6.pt', workers=8, world_size=1)
Start Tensorboard with "tensorboard --logdir runs/train", view at http://localhost:6006/
Hyperparameters {'lr0': 0.01, 'lrf': 0.2, 'momentum': 0.937, 'weight_decay': 0.0005, 'warmup_epochs': 3.0, 'warmup_momentum': 0.8, 'warmup_bias_lr': 0.1, 'box': 0.05, 'cls': 0.5, 'cls_pw': 1.0, 'obj': 1.0, 'obj_pw': 1.0, 'iou_t': 0.2, 'anchor_t': 4.0, 'fl_gamma': 0.0, 


                 all    1.23e+03    6.94e+03       0.439       0.822       0.714       0.522
                 all    1.23e+03    6.94e+03       0.467       0.849       0.723       0.538
                 all    1.23e+03    6.94e+03       0.476       0.804       0.738       0.558
                 all    1.23e+03    6.94e+03       0.522        0.79       0.747        0.57
                 all    1.23e+03    6.94e+03         0.5       0.837        0.76       0.581
                 all    1.23e+03    6.94e+03       0.494       0.813       0.758       0.579
                 all    1.23e+03    6.94e+03       0.509       0.885       0.782       0.595
                 all    1.23e+03    6.94e+03        0.51        0.83       0.771       0.606
                 all    1.23e+03    6.94e+03       0.534       0.825       0.781       0.608
                 all    1.23e+03    6.94e+03       0.522       0.847       0.779       0.609
                 all    1.23e+03    6.94e+03       0.534       0.911 


Scanning images:  35%|###5      | 8198/23417 [00:50<01:33, 163.60it/s]


Scanning images: 100%|##########| 23417/23417 [02:19<00:00, 167.54it/s]

0it [00:00, ?it/s]
Scanning labels ..\dataset\train-001\labels.cache3 (3702 found, 0 missing, 3 empty, 6 duplicate, for 23417 images): 3705it [00:00, 33975.01it/s]
Scanning labels ..\dataset\train-001\labels.cache3 (8090 found, 0 missing, 3 empty, 10 duplicate, for 23417 images): 8093it [00:00, 36950.90it/s]
Scanning labels ..\dataset\train-001\labels.cache3 (12312 found, 0 missing, 3 empty, 14 duplicate, for 23417 images): 12315it [00:00, 38235.22it/s]
Scanning labels ..\dataset\train-001\labels.cache3 (16638 found, 0 missing, 3 empty, 24 duplicate, for 23417 images): 16641it [00:00, 39523.07it/s]
Scanning labels ..\dataset\train-001\labels.cache3 (21244 found, 0 missing, 6 empty, 33 duplicate, for 23417 images): 21250it [00:00, 40246.21it/s]
Scanning labels ..\dataset\train-001\labels.cache3 (23411 found, 0 missing, 6 empty, 38 duplicate, for 23417 images): 23417it [00:00, 39642.40it/s]

Scanning images: 100%|##

...

      1/24     15.9G   0.02571   0.01167   0.02064   0.05803        70      1280:  90%|########9 | 2630/2928 [16:52<01:53,  2.62it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05803        70      1280:  90%|########9 | 2631/2928 [16:52<01:52,  2.63it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05802        34      1280:  90%|########9 | 2631/2928 [16:52<01:52,  2.63it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05802        34      1280:  90%|########9 | 2632/2928 [16:52<01:52,  2.63it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05802        71      1280:  90%|########9 | 2632/2928 [16:52<01:52,  2.63it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05802        71      1280:  90%|########9 | 2633/2928 [16:52<01:54,  2.57it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05802        59      1280:  90%|########9 | 2633/2928 [16:53<01:54,  2.57it/s]
      1/24     15.9G   0.02571   0.01167   0.02064   0.05802  

      2/24       16G   0.02411   0.01149   0.01739   0.05299        39      1280:  92%|#########2| 2695/2928 [17:13<01:28,  2.64it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

     18/24       16G   0.01365  0.008723  0.007003   0.02937        70      1280:  76%|#######5  | 2216/2928 [14:13<04:33,  2.60it/s]
     18/24       16G   0.01365  0.008723  0.007001   0.02937        58      1280:  76%|#######5  | 2216/2928 [14:14<04:33,  2.60it/s]
     18/24       16G   0.01365  0.008723  0.007001   0.02937        58      1280:  76%|#######5  | 2217/2928 [14:14<04:38,  2.55it/s]
     18/24       16G   0.01365  0.008723  0.007001   0.02937        72      1280:  76%|#######5  | 2217/2928 [14:14<04:38,  2.55it/s]
   

     19/24       16G    0.0133  0.008639  0.006343   0.02828        73      1280:  62%|######1   | 1813/2928 [11:38<07:06,  2.62it/s]
     19/24       16G    0.0133  0.008639  0.006344   0.02828        65      1280:  62%|######1   | 1813/2928 [11:38<07:06,  2.62it/s]
     19/24       16G    0.0133  0.008639  0.006344   0.02828        65      1280:  62%|######1   | 1814/2928 [11:38<07:06,  2.61it/s]
     19/24       16G    0.0133   0.00864  0.006344   0.02828        72      1280:  62%|######1   | 1814/2928 [11:38<07:06,  2.61it/s]
     19/24       16G    0.0133   0.00864  0.006344   0.02828        72      1280:  62%|######1   | 1815/2928 [11:38<07:03,  2.63it/s]
     19/24       16G    0.0133   0.00864  0.006343   0.02828        79      1280:  62%|######1   | 1815/2928 [11:39<07:03,  2.63it/s]
     19/24       16G    0.0133   0.00864  0.006343   0.02828        79      1280:  62%|######2   | 1816/2928 [11:39<07:02,  2.63it/s]
     19/24       16G    0.0133   0.00864  0.006342   0.02828  

     20/24       16G   0.01295  0.008435  0.006195   0.02758        39      1280:  78%|#######7  | 2275/2928 [14:35<04:11,  2.60it/s]
     20/24       16G   0.01295  0.008435  0.006195   0.02758        72      1280:  78%|#######7  | 2275/2928 [14:35<04:11,  2.60it/s]
     20/24       16G   0.01295  0.008435  0.006195   0.02758        72      1280:  78%|#######7  | 2276/2928 [14:35<04:12,  2.58it/s]
     20/24       16G   0.01295  0.008435  0.006196   0.02758        59      1280:  78%|#######7  | 2276/2928 [14:36<04:12,  2.58it/s]
     20/24       16G   0.01295  0.008435  0.006196   0.02758        59      1280:  78%|#######7  | 2277/2928 [14:36<04:08,  2.62it/s]
     20/24       16G   0.01295  0.008433  0.006196   0.02758        40      1280:  78%|#######7  | 2277/2928 [14:36<04:08,  2.62it/s]
     20/24       16G   0.01295  0.008433  0.006196   0.02758        40      1280:  78%|#######7  | 2278/2928 [14:36<04:06,  2.64it/s]
     20/24       16G   0.01295  0.008432  0.006196   0.02757  

     22/24       16G   0.01267  0.008616  0.005533   0.02682        96      1280:   3%|2         | 84/2928 [00:32<17:50,  2.66it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [33]:
# Start tensorboard
# Launch after you have started training
# logs save in the folder "runs"

# In Window CMD
# taskkill /im tensorboard.exe /f
# del /q %TMP%\.tensorboard-info\*
%reload_ext tensorboard 
%tensorboard --host localhost --logdir runs/train/yolor-220612

# Inference

In [34]:
!python detect.py --weights "runs/train/yolor-220612/weights/best.pt" --conf 0.5 --source "../dataset/test-002/images/00a78199-721b-4adb-9a65-d62226e4cfea.png" --names "../dataset/train-001/data.names" --save-txt --cfg cfg/yolor_p6.cfg

Namespace(agnostic_nms=False, augment=False, cfg='cfg/yolor_p6.cfg', classes=None, conf_thres=0.5, device='0', img_size=1280, iou_thres=0.5, names='../dataset/train-001/data.names', output='inference/output', save_txt=True, source='../dataset/test-002/images/00a78199-721b-4adb-9a65-d62226e4cfea.png', update=False, view_img=False, weights=['runs/train/yolor-220612/weights/best.pt'])
image 1/1 C:\Users\user\Desktop\jh\dataset\test-002\images\00a78199-721b-4adb-9a65-d62226e4cfea.png: 768x1280 2 세단(승용차)s, 1 SUVs, 1 트럭s, 1 성인s, Done. (0.033s)
Results saved to inference\output
Done. (1.226s)


C:\Users\user\anaconda3\envs\yolor\lib\site-packages\torch\functional.py:568: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  C:\cb\pytorch_1000000000000\work\aten\src\ATen\native\TensorShape.cpp:2228.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


# Test

In [35]:
# best.pt
!python test.py --device 0 --data "../dataset/train-001/data.yaml" --names "../dataset/train-001/data.names" --batch 16 --conf 0.5 --iou 0.65 --cfg cfg/yolor_p6.cfg --weights "runs/train/yolor-220612/weights/best.pt" --name yolor-test-220612-best --task test --save-json --save-conf

Namespace(augment=False, batch_size=16, cfg='cfg/yolor_p6.cfg', conf_thres=0.5, data='../dataset/train-001/data.yaml', device='0', exist_ok=False, img_size=1280, iou_thres=0.65, name='yolor-test-220612-best', names='../dataset/train-001/data.names', project='runs/test', save_conf=True, save_json=True, save_txt=False, single_cls=False, task='test', verbose=False, weights=['runs/train/yolor-220612/weights/best.pt'])
                 all    1.95e+04           0           0           0           0           0
Speed: 7.6/0.6/8.2 ms inference/NMS/total per 1280x1280 image at batch-size 16

Evaluating pycocotools mAP... saving runs\test\yolor-test-220612-best\best_predictions.json...
loading annotations into memory...
Done (t=0.40s)
creating index...
index created!
Loading and preparing results...
ERROR: pycocotools unable to run: Results do not correspond to current coco set
Results saved to runs\test\yolor-test-220612-best


Using torch 1.11.0 CUDA:0 (NVIDIA GeForce RTX 3090, 24575MB)

C:\Users\user\anaconda3\envs\yolor\lib\site-packages\torch\functional.py:568: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at  C:\cb\pytorch_1000000000000\work\aten\src\ATen\native\TensorShape.cpp:2228.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
Model Summary: 665 layers, 36908616 parameters, 36908616 gradients, 80.562121000 GFLOPS

0it [00:00, ?it/s]
Scanning labels ..\dataset\test-002\labels.cache3 (0 found, 0 missing, 19521 empty, 0 duplicate, for 19521 images): 19521it [00:00, 1219678.36it/s]

               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:   0%|          | 0/1221 [00:00<?, ?it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:   0%|          | 1/1221 [00:01<40:39,  2.00s/it]
               Class      Images     Targets   

               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  81%|########1 | 991/1221 [02:26<00:32,  7.01it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  81%|########1 | 992/1221 [02:26<00:34,  6.73it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  81%|########1 | 993/1221 [02:26<00:33,  6.79it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  81%|########1 | 994/1221 [02:26<00:33,  6.81it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  81%|########1 | 995/1221 [02:26<00:33,  6.83it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  82%|########1 | 996/1221 [02:26<00:32,  6.94it/s]
               Class      Images     Targets           P           R      mAP@.5  mAP@.5:.95:  82%|########1 | 997/1221 [02:27<00:

# Sample Submission

In [36]:
import json
from tqdm import tqdm

with open('../dataset/download1-20220607T050736Z-003/download1/test/Test_Images_Information.json', 'r', encoding='utf-8') as f:
    test_info = json.load(f)

with open('./runs/test/yolor-test-220612-best/best_predictions.json', 'r', encoding='utf-8') as f:
    prediction_json = json.load(f)

submission_jdict = []

for prediction in tqdm(prediction_json, desc='submission_json'):
    for test in test_info['images']:
        if test['file_name'].split('.')[0] == prediction['image_id']:
            submission_jdict.append({'image_id': test['id'],
                                     'category_id': prediction['category_id'] + 1,
                                     'bbox': prediction['bbox'],
                                     'score': prediction['score'],
                                     'segmentation': [[0, 0]],
                                     # 'area': prediction['bbox'][2] * prediction['bbox'][3]
                                    })

with open('./runs/test/yolor-test-220612-best/sample_submission.json', 'w', encoding='utf-8') as f:
    json.dump(submission_jdict, f)

submission_json: 100%|█████████████████████████████████████████████████████████| 73710/73710 [04:00<00:00, 306.68it/s]
